In [2]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score
import lightgbm as lgb
import optuna
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.impute import SimpleImputer
from lightgbm import early_stopping, log_evaluation



RANDOM_SEED = 42

train = pd.read_csv("./data/train.csv")
test = pd.read_csv("./data/test.csv")
test_ids = test["ID"] 

test["log_pSat_Pa"] = None
combined = pd.concat([train, test], ignore_index=True)

non_numeric_cols = combined.select_dtypes(include=['object']).columns
combined = pd.get_dummies(combined, columns=non_numeric_cols, drop_first=True)

train = combined[combined["log_pSat_Pa"].notnull()]
test = combined[combined["log_pSat_Pa"].isnull()]
y = train["log_pSat_Pa"]
X = train.drop(columns=["log_pSat_Pa"])
test = test.drop(columns=["log_pSat_Pa"])

imputer = SimpleImputer(strategy="mean")
X = pd.DataFrame(imputer.fit_transform(X), columns=X.columns)
test = pd.DataFrame(imputer.transform(test), columns=test.columns)

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=RANDOM_SEED)

def objective(trial):
    params = {
        'boosting_type': 'gbdt',
        'num_leaves': trial.suggest_int('num_leaves', 31, 255),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.1),
        'n_estimators': 3000,
        'max_depth': trial.suggest_int('max_depth', -1, 10),
        'feature_fraction': trial.suggest_uniform('feature_fraction', 0.6, 1.0),
        'bagging_fraction': trial.suggest_uniform('bagging_fraction', 0.6, 1.0),
        'lambda_l1': trial.suggest_loguniform('lambda_l1', 0.01, 1.0),
        'lambda_l2': trial.suggest_loguniform('lambda_l2', 0.01, 1.0),
        'random_state': RANDOM_SEED
    }
    model = lgb.LGBMRegressor(**params)
    model.fit(X_train, y_train, eval_set=[(X_val, y_val)], eval_metric='rmse', callbacks=[
            early_stopping(stopping_rounds=50),  # Stops if no improvement for 50 rounds
            log_evaluation(10)                  # Logs every 10 iterations
        ])
    preds = model.predict(X_val)
    return mean_squared_error(y_val, preds, squared=False)

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=50)
print("Best hyperparameters:", study.best_params)

/tmp/ipykernel_22682/4284407726.py:20: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  combined = pd.concat([train, test], ignore_index=True)
[I 2024-12-05 16:58:26,957] A new study created in memory with name: no-name-36125b3d-4df7-4148-8354-469859ffd752
/tmp/ipykernel_22682/4284407726.py:41: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.1),
/tmp/ipykernel_22682/4284407726.py:44: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/r

[LightGBM] [Warning] feature_fraction is set=0.877176779551444, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.877176779551444
[LightGBM] [Warning] lambda_l2 is set=0.04172112629141879, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.04172112629141879
[LightGBM] [Warning] lambda_l1 is set=0.014583466979919501, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.014583466979919501
[LightGBM] [Warning] bagging_fraction is set=0.6740004930743102, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6740004930743102
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] feature_fraction is set=0.877176779551444, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.877176779551444
[LightGBM] [Warning] lambda_l2 is set=0.04172112629141879, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.04172112629141879
[LightGBM] [Warning] lambda_l1 is set=0.014583466979919501, 

/home/lottatan/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-05 16:58:27,991] Trial 0 finished with value: 1.6398077146953243 and parameters: {'num_leaves': 150, 'learning_rate': 0.0443095537311846, 'max_depth': 1, 'feature_fraction': 0.877176779551444, 'bagging_fraction': 0.6740004930743102, 'lambda_l1': 0.014583466979919501, 'lambda_l2': 0.04172112629141879}. Best is trial 0 with value: 1.6398077146953243.
/tmp/ipykernel_22682/4284407726.py:41: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.1),
/tmp/ipykernel_22682/4284407726.p

[LightGBM] [Warning] feature_fraction is set=0.9708487586225225, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9708487586225225
[LightGBM] [Warning] lambda_l2 is set=0.1317374275399556, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.1317374275399556
[LightGBM] [Warning] lambda_l1 is set=0.8187904317865237, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.8187904317865237
[LightGBM] [Warning] bagging_fraction is set=0.6118798135837918, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6118798135837918
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] feature_fraction is set=0.9708487586225225, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9708487586225225
[LightGBM] [Warning] lambda_l2 is set=0.1317374275399556, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.1317374275399556
[LightGBM] [Warning] lambda_l1 is set=0.8187904317865237, reg_al

/home/lottatan/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-05 16:58:29,329] Trial 1 finished with value: 1.575062719142975 and parameters: {'num_leaves': 137, 'learning_rate': 0.01946378981472684, 'max_depth': 10, 'feature_fraction': 0.9708487586225225, 'bagging_fraction': 0.6118798135837918, 'lambda_l1': 0.8187904317865237, 'lambda_l2': 0.1317374275399556}. Best is trial 1 with value: 1.575062719142975.


...

[370]	valid_0's rmse: 1.57211	valid_0's l2: 2.47152
[380]	valid_0's rmse: 1.57206	valid_0's l2: 2.47138
[390]	valid_0's rmse: 1.57189	valid_0's l2: 2.47085
[400]	valid_0's rmse: 1.57141	valid_0's l2: 2.46932
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[410]	valid_0's rmse: 1.57189	valid_0's l2: 2.47083
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[420]	valid_0's rmse: 1.57215	valid_0's l2: 2.47165
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[430]	valid_0's rmse: 1.57196	valid_0's l2: 2.47105
[440]	valid_0's rmse: 1.5721	valid_0's l2: 2.4715
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[450]	valid_0's rmse: 1.57174	valid_0's l2: 2.47036
Early stopping, best iteration is:
[402]	valid_0's rmse: 1.57137	valid_0's l2: 2.4692
[LightGBM] [Warning] feature_fraction is set=0.9038427716551802, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.90384277165

/tmp/ipykernel_22682/4284407726.py:41: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.1),
/tmp/ipykernel_22682/4284407726.py:44: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.
  'feature_fraction': trial.suggest_uniform('feature_fraction', 0.6, 1.0),
/tmp/ipykernel_22682/4284407726.py:45: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.
  'bagging_fraction': trial.suggest_uniform('bagging_fraction', 0.6, 1.0),
/tmp/ipykernel_22682/4284407726.py:46: FutureWarning: suggest_loguniform has been

[LightGBM] [Warning] feature_fraction is set=0.8641801751487683, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8641801751487683
[LightGBM] [Warning] lambda_l2 is set=0.010393494539956423, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.010393494539956423
[LightGBM] [Warning] lambda_l1 is set=0.05587374126847258, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.05587374126847258
[LightGBM] [Warning] bagging_fraction is set=0.8847446225740452, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8847446225740452
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] feature_fraction is set=0.8641801751487683, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8641801751487683
[LightGBM] [Warning] lambda_l2 is set=0.010393494539956423, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.010393494539956423
[LightGBM] [Warning] lambda_l1 is set=0.05587374126847

/home/lottatan/.pyenv/versions/3.10.13/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-05 16:59:42,122] Trial 49 finished with value: 1.5742960500681888 and parameters: {'num_leaves': 60, 'learning_rate': 0.025485931915827886, 'max_depth': 8, 'feature_fraction': 0.8641801751487683, 'bagging_fraction': 0.8847446225740452, 'lambda_l1': 0.05587374126847258, 'lambda_l2': 0.010393494539956423}. Best is trial 46 with value: 1.5700783260915219.


Best hyperparameters: {'num_leaves': 64, 'learning_rate': 0.021729739927956977, 'max_depth': 8, 'feature_fraction': 0.9037198623786143, 'bagging_fraction': 0.8947034762229957, 'lambda_l1': 0.041340954601109994, 'lambda_l2': 0.01639667141285937}
